-----------------------------------------------------------------

# Các bước thực hiện gán nhãn cho 1 câu  comment
## 1. Thống kê tổng quan các từ trong các câu được sử dụng nhiều nhất.
## 2. Sử dụng Deep Learning, mạng RNN để gãn nhán cho 1 câu.
## 3. Khi mô hình đã có sự ổn định, đẩy các sự dự đoán đó lên postgresl của server.
------------------------------------------------------------------------------------------------------------------



## 1. Thống kế tổng quan các từ


Trước tiên import vào các thư viện cần xử lý.
* Thư viện openpyxl để xử lý với file excel trong python.
* Thư viện pyvi để phân loại từ loại các từ trong câu.

In [20]:
import openpyxl
from pyvi import ViTokenizer, ViPosTagger


pos_dict = {"A": "Tính từ", "E": "Giới từ", "I": "Thán từ", "L": "Từ xác định", "M": "Chữ số", "N": "Danh từ chung",
            "Nc": "Danh từ phân loại", "Ny": "Danh từ viết tắt", "Np": "Danh từ riêng", "Nu": "Danh từ đơn vị",
            "P": "Đại từ", "R": "Trạng từ", "V": "Động từ", "X": "Không rõ", "F": "Dấu câu", "C": "Liên từ",
            "S": "Liên từ phụ", "T": "Từ phụ trợ"}

def get_pos_tagging(string):
    return ViPosTagger.postagging(ViTokenizer.tokenize(u""+string))

In [21]:
# Load file dữ liệu excel vào môi trường Python.
wb = openpyxl.load_workbook('./foody-data-1531-26072018.xlsx')

In [22]:
comments_sheet_name = wb.sheetnames[1]

In [23]:
comments_sheet_name

'Cmts'

In [24]:
comments_worksheet = wb[comments_sheet_name]
comments_worksheet

<Worksheet "Cmts">

Ở đây mình đã có xử lý các từ stop-word(chẳng hạn các từ nè, này, nha,...) các từ không có ý nghĩa nhiều lắm trong câu và lưu vào file có tên là stop_words_vietnamese.pickle 

In [25]:
import pickle
import os
pickle_in = open("/".join(os.getcwd().split('/')[:-1])+ "/stop_words_vietnamese.pickle", "rb")
list_stop_word = pickle.load(pickle_in)

Qua quan sát trên bộ dữ liệu thì mình thấy những từ viết tắt này thông dụng nhất, nên mình đưa vào để xử lý những từ viết tắt thông dụng

In [26]:
pickle_in = open("/".join(os.getcwd().split('/')[:-1])+ "/abbreviation_words_vietnamese.pickle", "rb")
abbreviation = pickle.load(pickle_in)

Xử lý dữ liệu để đưa ra thống kê, đưa câu comment về chữ in thường hết, bỏ các dấu câu không cần thiết và ký tự đặc biệt, đưa 1 số từ viết tắt thông dụng về từ chính.

In [37]:
statistic_words = dict()
statistic_pos = dict()
statistic_overview = dict()
count = 1
import string
for row in range(2, comments_worksheet.max_row + 1):
    for column in "I": # get only the column I in the sheet
        cell_name = "{}{}".format(column, row)
        cell_val = comments_worksheet[cell_name].value
        if cell_val is not None and type(cell_val) is str:
            for p in string.punctuation:
                if p == "_" or p == "^" or p == "<" or p == ">":
                    continue
                cell_val = cell_val.replace(p, "")
            print(count, cell_val)
            cell_val = get_pos_tagging(cell_val)
            words, pos = cell_val[0], cell_val[1]
            print(words, pos)
            for ch, p in zip(words, pos):
                if (ch in abbreviation and abbreviation[ch] in list_stop_word) or \
                        ch in list_stop_word or not ch.isalnum():
                    continue
                if not p.startswith("N"):
                    ch = ch.lower()
                if ch in abbreviation:
                    ch = abbreviation[ch]
                if pos_dict[p] not in statistic_pos:
                    statistic_pos[pos_dict[p]] = 0
                if ch not in statistic_words:
                    statistic_words[ch] = 0
                if pos_dict[p] not in statistic_overview:
                    statistic_overview[pos_dict[p]] = set()
                statistic_words[ch] += 1
                statistic_pos[pos_dict[p]] += 1
                statistic_overview[pos_dict[p]].add(ch)
        count += 1

1 thứ 5 vui vẻ và tràn đầy năng lượng nha Foodyvn <3
['thứ', '5', 'vui_vẻ', 'và', 'tràn_đầy', 'năng_lượng', 'nha', 'Foodyvn', '<', '3'] ['N', 'M', 'A', 'C', 'V', 'N', 'N', 'Np', 'F', 'M']
2 A nào chát video không
['A', 'nào', 'chát', 'video', 'không'] ['N', 'P', 'V', 'N', 'R']
3 nogn
['nogn'] ['N']
4 Phạm Rin Bao Nhu mua cái nì
['Phạm_Rin', 'Bao_Nhu_mua', 'cái', 'nì'] ['Np', 'V', 'Nc', 'N']
5 Nhung Kim Kushorangee Kẻ quát dallas haha
['Nhung_Kim_Kushorangee', 'Kẻ', 'quát', 'dallas', 'haha'] ['Nc', 'Np', 'V', 'N', 'V']
6 Tố Trinh nà 😐😐😐
['Tố_Trinh', 'nà', '😐', '😐', '😐'] ['Np', 'V', 'N', 'V', 'N']
7 Tới sn t tặng t nha Nguyễn Thùy
['Tới', 'sn', 't', 'tặng', 't', 'nha', 'Nguyễn_Thùy'] ['E', 'N', 'N', 'V', 'N', 'N', 'Np']
8 An pâu hay ăn dallas
['An_pâu', 'hay', 'ăn_dallas'] ['N', 'C', 'V']
9 Ngọc Phạm🙁
['Ngọc_Phạm_🙁'] ['Np']
10 Ăn đòn haha
['Ăn_đòn', 'haha'] ['N', 'V']
11 Nga Phi Bui
['Nga', 'Phi_Bui'] ['Np', 'Np']
12 Ăn bánh ướt
['Ăn', 'bánh_ướt'] ['V', 'N']
13 Tiên Tiên nhớ tặng sinh nh

['ngon', 'quá'] ['A', 'R']
285 tuyệt vời
['tuyệt_vời'] ['A']
286 Nguyễn Ánh
['Nguyễn_Ánh'] ['Np']
287 Panda Nguyen Nguyễn Hân Nguyễn Giang Sheryl Tang Thư Thư Nhi Đan t thèm quá bây
['Panda_Nguyen', 'Nguyễn_Hân', 'Nguyễn_Giang', 'Sheryl_Tang', 'Thư_Thư_Nhi', 'Đan_t', 'thèm', 'quá', 'bây'] ['Np', 'Np', 'Np', 'Np', 'Np', 'V', 'V', 'R', 'A']
288 Tôn Thất Thành Khắc
['Tôn_Thất_Thành_Khắc'] ['Np']
289 bữa làm làm 1 bữa cưng ơi huhuuu
['bữa', 'làm', 'làm', '1', 'bữa', 'cưng', 'ơi', 'huhuuu'] ['N', 'V', 'V', 'M', 'N', 'V', 'T', 'N']
290 Huỳnh Trung Quân chỗ gần trg e nè
['Huỳnh_Trung_Quân', 'chỗ', 'gần', 'trg', 'e', 'nè'] ['V', 'N', 'A', 'N', 'V', 'N']
291 Cũng kiểu dzay á Lên sài gòn vào cuối tuần lại đi dẫn đi thêm 10 món nữa
['Cũng', 'kiểu', 'dzay', 'á', 'Lên', 'sài_gòn', 'vào', 'cuối', 'tuần', 'lại', 'đi', 'dẫn', 'đi', 'thêm', '10', 'món', 'nữa'] ['R', 'N', 'N', 'V', 'V', 'N', 'E', 'N', 'N', 'R', 'R', 'V', 'V', 'V', 'M', 'N', 'R']
292 Có canh bún mẹ tôi kìa Thử đi
['Có', 'canh', 'bún', 'm

['Phan_Ngọc'] ['Np']
413 Tịnh Yên
['Tịnh_Yên'] ['Np']
414 Ngọc LươngHuỳnh Phụng
['Ngọc_LươngHuỳnh', 'Phụng'] ['N', 'Np']
415 Phạm Khanh
['Phạm_Khanh'] ['Np']
416 Cái lẩu 120k ah 1con sao đủ
['Cái', 'lẩu', '120k', 'ah', '1con', 'sao', 'đủ'] ['Nc', 'N', 'M', 'N', 'M', 'P', 'A']
417 Phởn Phanh cùng ăn nào
['Phởn_Phanh', 'cùng', 'ăn', 'nào'] ['Np', 'A', 'V', 'R']
418 Thành Nguyễn
['Thành', 'Nguyễn'] ['V', 'Np']
419 Trân Phạm
['Trân_Phạm'] ['Np']
420 tôm hùm mà rẻ thì thường ko có ngon
['tôm_hùm', 'mà', 'rẻ', 'thì', 'thường', 'ko', 'có', 'ngon'] ['N', 'C', 'A', 'C', 'R', 'V', 'V', 'A']
421 Bao thì đi nà
['Bao', 'thì', 'đi', 'nà'] ['P', 'C', 'V', 'V']
422 Lee Ween nhứt nách luôn
['Lee_Ween_nhứt', 'nách', 'luôn'] ['N', 'N', 'R']
423 Có lý đo
['Có_lý', 'đo'] ['A', 'V']
424 Đmm 
['Đmm'] ['Np']
425 Yaaaaaaassssss❤️
['Yaaaaaaassssss', '❤', '️'] ['Np', 'V', 'N']
426 Gần lắm chừng nào đc
['Gần', 'lắm', 'chừng', 'nào', 'đc'] ['A', 'R', 'N', 'P', 'V']
427 ăn đi đừng chửi 
['ăn', 'đi', 'đừng', 'chửi']

['Chẹp', 'chẹp', 'muốn', 'ăn', 'quá', 'à'] ['N', 'N', 'V', 'V', 'R', 'A']
553 Di 
['Di'] ['Np']
554 Nguyễn Tùng cuối tuần triển thôi
['Nguyễn_Tùng', 'cuối', 'tuần', 'triển', 'thôi'] ['N', 'N', 'N', 'N', 'V']
555 Ốc Lố Hồ Nguyên Mai Hương đi ăn thử đi
['Ốc_Lố', 'Hồ_Nguyên', 'Mai_Hương', 'đi', 'ăn', 'thử', 'đi'] ['Np', 'Np', 'Np', 'V', 'V', 'V', 'V']
556 Đặng Thị Kim Thuỳ vo r anh dat di ne em an lau anh an tom hum hi hi
['Đặng_Thị_Kim_Thuỳ', 'vo', 'r', 'anh', 'dat', 'di_ne', 'em', 'an', 'lau', 'anh', 'an', 'tom', 'hum', 'hi_hi'] ['Np', 'V', 'N', 'N', 'V', 'V', 'N', 'A', 'V', 'N', 'V', 'N', 'E', 'N']
557 Nguyễn Ngọc Thạnh hơ hơ Z anh đi ăn 1m di nhé😒
['Nguyễn_Ngọc_Thạnh', 'hơ', 'hơ', 'Z', 'anh', 'đi', 'ăn', '1m', 'di', 'nhé', '😒'] ['Np', 'V', 'N', 'Ny', 'N', 'V', 'V', 'M', 'V', 'T', 'N']
558 Tí Ca
['Tí_Ca'] ['Np']
559 Đặng Thị Kim Thuỳ thui ma em di theo co nguoi quay clip cho a review mon an cho
['Đặng_Thị_Kim_Thuỳ', 'thui', 'ma_em', 'di', 'theo', 'co', 'nguoi', 'quay', 'clip', 'cho', '

677 Nhu Y Bui Thi
['Nhu_Y_Bui_Thi'] ['Np']
678 Má Chứ m đòi to bỏ vài triệu ra con
['Má', 'Chứ', 'm', 'đòi', 'to', 'bỏ', 'vài', 'triệu', 'ra', 'con'] ['N', 'Np', 'V', 'V', 'A', 'V', 'L', 'M', 'V', 'N']
679 Ủa sao ghi cũng to mà
['Ủa', 'sao', 'ghi', 'cũng', 'to', 'mà'] ['V', 'P', 'V', 'R', 'A', 'C']
680 nghi lắm dm 
['nghi', 'lắm', 'dm'] ['A', 'R', 'A']
681 lẩu có 2 con  tôm chít xíu haiizz
['lẩu', 'có', '2', 'con', 'tôm', 'chít', 'xíu', 'haiizz'] ['N', 'V', 'M', 'Nc', 'N', 'V', 'V', 'N']
682 An mot hoi 5 con tom hum nuong moi da doi
['An', 'mot', 'hoi', '5', 'con', 'tom', 'hum', 'nuong_moi', 'da_doi'] ['Np', 'V', 'N', 'M', 'Nc', 'N', 'V', 'N', 'V']
683 Đi thôi
['Đi', 'thôi'] ['V', 'V']
684 Coleen Ti
['Coleen_Ti'] ['Np']
685 Kim Lê m ăn chưa Này lẩu 2 ng mà
['Kim_Lê_m', 'ăn', 'chưa', 'Này', 'lẩu', '2', 'ng', 'mà'] ['N', 'V', 'R', 'P', 'N', 'M', 'N', 'C']
686 đứa con ăn hk đã kk
['đứa', 'con', 'ăn', 'hk', 'đã', 'kk'] ['Nc', 'N', 'V', 'N', 'R', 'V']
687 Kim Lê bỏ tiền ra nhiu cũng có ăn c

...

['Ăn', 'này', 'nè', 'Sam_Lee'] ['V', 'P', 'N', 'Np']
48072 Ko ngon ak vợ
['Ko', 'ngon', 'ak', 'vợ'] ['N', 'A', 'V', 'N']
48073 Đỗ Thị Minh Lý Chanh Chua
['Đỗ_Thị_Minh_Lý', 'Chanh_Chua'] ['Np', 'Np']
48074 6k luôn ak chị
['6k', 'luôn', 'ak', 'chị'] ['M', 'R', 'V', 'N']
48075 Ngonahihi
['Ngonahihi'] ['Np']
48077 Thanhtam Huynhngoc pin iu ah 😍
['Thanhtam_Huynhngoc', 'pin', 'iu', 'ah', '😍'] ['Np', 'V', 'N', 'V', 'N']
48078 Phê Phê bà cố con Hạ mới đúc cho ă nè ngon đã lun😍😍😍😍😍
['Phê_Phê', 'bà', 'cố', 'con', 'Hạ_mới', 'đúc', 'cho', 'ă', 'nè', 'ngon', 'đã', 'lun', '😍', '😍', '😍', '😍', '😍'] ['V', 'N', 'V', 'Nc', 'N', 'V', 'E', 'N', 'N', 'A', 'R', 'V', 'N', 'V', 'N', 'V', 'N']
48079 Nhìn mà thèmBữa nhà em say sinh tố làm ngon lắm 😂😂😂 Bich Ngoc Bich Ngoc
['Nhìn', 'mà', 'thèmBữa', 'nhà', 'em', 'say', 'sinh_tố', 'làm', 'ngon', 'lắm', '😂', '😂', '😂', 'Bich_Ngoc', 'Bich_Ngoc'] ['V', 'C', 'V', 'N', 'N', 'V', 'N', 'V', 'A', 'R', 'V', 'N', 'N', 'Np', 'Np']
48080 Ở Tân Bình cũng có bánh xèo rẻ vậy hả 
['

['Thanh_Hiền'] ['Np']
48339 Anh Dinh gần nhà e nè
['Anh', 'Dinh', 'gần', 'nhà', 'e', 'nè'] ['Nc', 'Np', 'A', 'N', 'V', 'N']
48340 Oke
['Oke'] ['Np']
48341 ngon quá
['ngon', 'quá'] ['A', 'R']
48342 Chổ mới
['Chổ', 'mới'] ['Np', 'R']
48343 Triển liền đi 😂
['Triển', 'liền', 'đi', '😂'] ['V', 'R', 'V', 'V']
48344 😮😮😮
['😮', '😮', '😮'] ['N', 'V', 'N']
48345 Hong My
['Hong_My'] ['Np']
48346 Bích Lê Thanh Phương
['Bích_Lê_Thanh_Phương'] ['Np']
48347 Ngon ớ 3
['Ngon', 'ớ', '3'] ['A', 'N', 'M']
48348 Lam Nguyễn save dô chếeeeee đẹp
['Lam', 'Nguyễn_save', 'dô', 'chếeeeee', 'đẹp'] ['Np', 'V', 'N', 'N', 'A']
48349 Gà Chổi Lông
['Gà', 'Chổi_Lông'] ['N', 'Np']
48350 Thuý Hằng Lê mở tiệm hồi nào vậy bà chị
['Thuý', 'Hằng', 'Lê_mở', 'tiệm', 'hồi', 'nào', 'vậy', 'bà', 'chị'] ['N', 'Np', 'V', 'N', 'N', 'P', 'P', 'N', 'N']
48351 Vương Nguyễn
['Vương_Nguyễn'] ['Np']
48352 Thèm vl 🙂
['Thèm', 'vl', '🙂'] ['V', 'V', 'N']
48353 Thanh Phương xem xong t chỉ muốn đi liền
['Thanh_Phương', 'xem', 'xong', 't', 'chỉ', '

['Liên', 'Nguyễn_tối', 'nay', 'uống', 'nữa', 'đi'] ['Np', 'V', 'P', 'V', 'R', 'V']
48535 Thanh Nhàn cho vui thôi ^^
['Thanh_Nhàn', 'cho', 'vui', 'thôi', '^', '^'] ['Np', 'E', 'A', 'T', 'F', 'F']
48536 Cốc cốc cốc cốc
['Cốc_cốc_cốc_cốc'] ['N']
48537 ngon
['ngon'] ['A']
48538 Phạm Lân
['Phạm_Lân'] ['Np']
48539 Uh c cũng chưa uống
['Uh_c', 'cũng', 'chưa', 'uống'] ['N', 'R', 'R', 'V']
48540 Vyy Khánh
['Vyy_Khánh'] ['Np']
48541 Hoang Yen rảnh đi mua đi 2 ce minh sẽ đc uống 😁
['Hoang_Yen', 'rảnh', 'đi', 'mua', 'đi', '2', 'ce', 'minh', 'sẽ', 'đc', 'uống', '😁'] ['N', 'A', 'V', 'V', 'R', 'M', 'N', 'N', 'R', 'V', 'V', 'N']
48542 Ngọc Hân Nguyễn
['Ngọc_Hân', 'Nguyễn'] ['Np', 'Np']
48543 hết thèm   đợi đẻ xong chắc thèm lại kkk
['hết', 'thèm', 'đợi', 'đẻ', 'xong', 'chắc', 'thèm', 'lại', 'kkk'] ['V', 'N', 'V', 'V', 'V', 'R', 'V', 'R', 'V']
48544 hay
['hay'] ['C']
48545 Huỳnh Quốc Mỹ Ái
['Huỳnh_Quốc_Mỹ_Ái'] ['Np']
48546 Ngọc Diệu
['Ngọc_Diệu'] ['Np']
48547 ngon
['ngon'] ['A']
48549 Đặt đi heo
['Đặt'

['Phạm_Thịnh'] ['Np']
48722 Áp dụng lần đầu đặt à
['Áp_dụng', 'lần', 'đầu', 'đặt', 'à'] ['V', 'N', 'N', 'V', 'N']
48723 A đặt mấy lần ùi 😞
['A', 'đặt', 'mấy', 'lần', 'ùi', '😞'] ['Ny', 'V', 'L', 'N', 'V', 'N']
48724 Điên 🙂 k giảm đâu
['Điên', '🙂_k', 'giảm', 'đâu'] ['Np', 'V', 'V', 'R']
48725 Trưa mai nhé
['Trưa', 'mai', 'nhé'] ['N', 'N', 'N']
48726 Huhuhu
['Huhuhu'] ['Np']
48727 Áp dụng cho nick mới gái oie
['Áp_dụng', 'cho', 'nick', 'mới', 'gái', 'oie'] ['V', 'E', 'N', 'A', 'N', 'A']
48728 Hoàng Thảo
['Hoàng_Thảo'] ['Np']
48729 Sương Bảo Phượng Minh Tag cho biết 
['Sương_Bảo', 'Phượng_Minh_Tag', 'cho', 'biết'] ['N', 'Np', 'V', 'V']
48731 Quỳnh Anh mai đặt gongcha đi
['Quỳnh_Anh', 'mai', 'đặt', 'gongcha', 'đi'] ['Np', 'N', 'V', 'N', 'V']
48732 1km bao nhiêu tiền ship
['1km', 'bao_nhiêu', 'tiền', 'ship'] ['M', 'P', 'N', 'V']
48733 Hảo Nguyễn mưa r nhĩ haizz
['Hảo', 'Nguyễn_mưa', 'r', 'nhĩ', 'haizz'] ['Np', 'V', 'N', 'V', 'N']
48734 Dở lắm luôn
['Dở', 'lắm', 'luôn'] ['A', 'R', 'R']
48735 

48984 Nay ứng luong rồi mà 😀😀😀😀
['Nay', 'ứng', 'luong', 'rồi', 'mà', '😀', '😀', '😀', '😀'] ['P', 'V', 'N', 'C', 'C', 'N', 'V', 'N', 'V']
48985 Trời ui mấy bua này ở đây mua bosau riêngcherrytum lum hết tiền rui
['Trời', 'ui', 'mấy', 'bua', 'này', 'ở', 'đây', 'mua', 'bosau', 'riêngcherrytum', 'lum', 'hết', 'tiền', 'rui'] ['N', 'V', 'L', 'N', 'P', 'E', 'P', 'V', 'N', 'N', 'V', 'V', 'N', 'V']
48986 Ăn sang chảnh wá hi Sr bao nhiu 1kg c
['Ăn', 'sang', 'chảnh', 'wá', 'hi', 'Sr', 'bao', 'nhiu', '1kg', 'c'] ['V', 'V', 'N', 'V', 'N', 'Np', 'V', 'N', 'M', 'N']
48987 Hảo Nguyễn xin lỗi chủ tài khoản vừa mới thức làm bạn phải đợi cmn lâu
['Hảo', 'Nguyễn', 'xin_lỗi', 'chủ', 'tài_khoản', 'vừa', 'mới', 'thức', 'làm_bạn', 'phải', 'đợi', 'cmn', 'lâu'] ['Np', 'Np', 'V', 'N', 'N', 'R', 'R', 'V', 'R', 'V', 'V', 'N', 'A']
48988 C thời mua dùm nènhà bà con c thoi trongko phun thuocri 6 60000sr thai 75000
['C_thời', 'mua', 'dùm', 'nènhà', 'bà_con', 'c', 'thoi', 'trongko', 'phun', 'thuocri', '6', '60000sr', 't

In [38]:
top_50_popular_words = sorted(statistic_words.items(), key=lambda x: x[1], reverse=True)[:50]
max_length_1 = len(max(top_50_popular_words, key=lambda x: len(x[0]))[0])
max_length_2 = len(max(set(pos_dict[get_pos_tagging(t[0])[1][0]] for t in top_50_popular_words), key=len))
print("Top 50 popular words:")
for v in top_50_popular_words:
    t_ = get_pos_tagging(v[0])[1]
    print("Chữ:", v[0] + " "*(max_length_1 - len(v[0])), 
          " | Loại:", pos_dict[t_[0]] + " "*(max_length_2 - len(pos_dict[t_[0]])), " | Tần suất xuất hiện:", v[1])

Top 50 popular words:
Chữ: đi      | Loại: Động từ        | Tần suất xuất hiện: 9230
Chữ: ngon    | Loại: Tính từ        | Tần suất xuất hiện: 2128
Chữ: mày     | Loại: Danh từ chung  | Tần suất xuất hiện: 1414
Chữ: tao     | Loại: Động từ        | Tần suất xuất hiện: 1228
Chữ: thèm    | Loại: Động từ        | Tần suất xuất hiện: 751
Chữ: mua     | Loại: Động từ        | Tần suất xuất hiện: 705
Chữ: đẹp     | Loại: Tính từ        | Tần suất xuất hiện: 705
Chữ: lắm     | Loại: Trạng từ       | Tần suất xuất hiện: 645
Chữ: 1       | Loại: Chữ số         | Tần suất xuất hiện: 630
Chữ: chỗ     | Loại: Danh từ chung  | Tần suất xuất hiện: 571
Chữ: 2       | Loại: Chữ số         | Tần suất xuất hiện: 568
Chữ: mấy     | Loại: Từ xác định    | Tần suất xuất hiện: 563
Chữ: Anh     | Loại: Danh từ chung  | Tần suất xuất hiện: 562
Chữ: ẩn      | Loại: Động từ        | Tần suất xuất hiện: 489
Chữ: bữa     | Loại: Danh từ chung  | Tần suất xuất hiện: 486
Chữ: hả      | Loại: Trạng từ       | Tần su

Thống kê tổng quan các loại từ

In [39]:
max_length_1 = len(max(statistic_pos.keys(), key=len))
for k, v in statistic_pos.items():
    print(k + " "*(max_length_1 - len(k)), v)
total_str = "Tổng cộng"
print("-"*(max_length_1 + 6))
print(total_str + " "*(max_length_1 - len(total_str)), sum(statistic_pos.values()))

Giới từ           866
Danh từ viết tắt  1356
Từ xác định       606
Đại từ            2147
Tính từ           7751
Liên từ           554
Danh từ riêng     12449
Từ phụ trợ        196
Trạng từ          2816
Liên từ phụ       12
Danh từ chung     33617
Danh từ đơn vị    100
Chữ số            3811
Không rõ          4
Động từ           36775
Thán từ           4
Danh từ phân loại 1671
-----------------------
Tổng cộng         104735


Các từ nằm trong từng loại từ 

In [40]:
for k, v in statistic_overview.items():
    print(k, ":")
    print(v)

Giới từ :
{'hả', 'lên', 'mày', 'za', 'từ', 'chu', 'đến', 'ak', 'trước', 'hoanh', 'hùi', 'rũ', 'luônà', 'tới', 'bằng', 'sau', 'thooiii', 'bởi', 'zay', 'mùa', 'do', 'hum', 'với', 'nhin', 'vì', 'of', 'xiu', 'ngjir', 'giu', 'ở', 'tater', 'siro', 'vô', 'qua', 'trong', 'chuuuu', 'nhờ', 'theo', 'chuột', 'duoc', 'het', 'nhiu', 'tận', 'thit', 'zũng', 'brian', 'mon', 'đim', 'cho', 'vs', 'hap', 'ngoài', 'về', 'ngon', 'của', 'trên', 'ủa', 'chac', 'hường', 'choi', 'quôc', 'tại', 'hino', 'nhân', 'dưới', 'để', 'giữa', 'dù', 'q4', 'the', 'wand', 'map', 'vào', 'ngoai'}
Danh từ viết tắt :
{'XX', 'VH', 'VA', 'CS', 'PH', 'Ờ', 'ĐL', 'NHÉ', 'CD', 'MÓN', 'TU', 'AOA', 'X', 'FA', 'TD', 'T8', 'CAM', 'DO', 'ĐÀ', 'Ợ', 'Ô', 'YEH', 'NGONQ', 'TM', 'MC', 'YOLO', 'TP', 'DN', 'SỢ', 'BD', 'VY', 'CHÈ', 'GV', 'NP', 'LE', 'VÕ', 'A2', 'C2', 'K', 'NT', 'TC', 'MAI', 'HANDMADE', 'BIẾT', 'MY', 'TL', 'HCM', 'SAO', 'MRT', 'GL', 'BH', 'DƯ', 'BĐ', 'ĐAU', 'PI', 'HT', 'KV', 'QUƠI', 'ĐT', 'PY', 'LÀ', 'PC', 'M', 'YK', 'QMT', 'HB', 'PCL

## 2. Sử dụng deep learning, RNN để gán nhãn cho 1 câu.


... to be continued ...

## 3. Đánh giá lại mô hình.


... to be continued ...
